# Building tweet vectorizer using dense vectors (Word2Vec)

In [1]:
import pandas as pd
from sklearn.metrics import f1_score
import pickle

from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.tokenize import TweetTokenizer
from gensim.models.word2vec import Word2Vec
from sklearn.linear_model import LogisticRegression

from tools import generate_dense_features

In [2]:
upstream = []
random_seed = 42

In [3]:
# Parameters
random_seed = 42
product = {
    "nb": "/Users/mboussarov/_umsi/Capstone/umads_697_data_medics/pipeline/output/vectorizer_dense.ipynb"
}


## Read the train and test data

In [4]:
df_train = pd.read_csv('../data/HumAID_data_v1.0/all_combined/all_train.tsv', sep='\t')
df_test = pd.read_csv('../data/HumAID_data_v1.0/all_combined/all_test.tsv', sep='\t')

df_train.dropna(inplace=True)
df_test.dropna(inplace=True)

df_train.sample(5)

tweet_id                                         tweet_text  \
41240   910540625556025344  RT @WSJ: Death toll from Mexico earthquake ris...   
1766   1034779083802963969  RT @KKAjith_FC: Coimbatore Thala Ajith Fans di...   
3731   1032189288555802624  Would be nice if Kerala remembers all these an...   
23100   913496872920039424  RT @homegypsy: Exclusive: Island of Vieques Vi...   
45431  1177129332327821313  A proud moment for #Pakistan as Prime Minister...   

                                  class_label  
41240                  injured_or_dead_people  
1766   rescue_volunteering_or_donation_effort  
3731                         not_humanitarian  
23100       infrastructure_and_utility_damage  
45431                        not_humanitarian

## Build and train the vectorizer and obtain the respective analyzer

In [5]:
tokenizer = TweetTokenizer(preserve_case=False, reduce_len=True, strip_handles=True)

vectorizer = TfidfVectorizer(
        tokenizer=tokenizer.tokenize, #tokenize_text,
        strip_accents='unicode',
        ngram_range=(1, 2),
        max_df=0.90,
        min_df=1,
        max_features=10000,
        use_idf=True
    )

In [6]:
%%time
vectorizer.fit(df_train['tweet_text'])

/Users/mboussarov/Library/Caches/pypoetry/virtualenvs/data-medics-capstone-ZGa4TAVF-py3.9/lib/python3.9/site-packages/sklearn/feature_extraction/text.py:524: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


CPU times: user 11.4 s, sys: 148 ms, total: 11.5 s
Wall time: 11.5 s


TfidfVectorizer(max_df=0.9, max_features=10000, ngram_range=(1, 2),
                strip_accents='unicode',
                tokenizer=<bound method TweetTokenizer.tokenize of <nltk.tokenize.casual.TweetTokenizer object at 0x7fb7e8e21cd0>>)

In [7]:
analyzer = vectorizer.build_analyzer()

In [8]:
tokens = [analyzer(s) for s in list(df_train['tweet_text'])]
tokens[100]

['rt',
 ':',
 'flood',
 'death',
 'toll',
 'touches',
 '239',
 'as',
 'kerala',
 'faces',
 'long',
 'road',
 'to',
 'recovery',
 '#keralafloods2018',
 '#keralafloods',
 'rt :',
 ': flood',
 'flood death',
 'death toll',
 'toll touches',
 'touches 239',
 '239 as',
 'as kerala',
 'kerala faces',
 'faces long',
 'long road',
 'road to',
 'to recovery',
 'recovery #keralafloods2018',
 '#keralafloods2018 #keralafloods']

## Init the dense vectorizer

In [9]:
quick_model = Word2Vec(sentences=tokens, vector_size=100, window=2,
                       min_count=10, workers=4, seed=random_seed)

In [10]:
quick_model.wv.get_vector('quake')

array([ 0.7072274 , -0.4604932 ,  0.00429265, -0.44627872,  0.21322207,
        1.3047371 ,  0.18295486,  0.2718335 ,  0.23268256, -0.66688365,
       -0.12375582, -0.8318188 ,  0.8527734 ,  0.22273897,  0.03672171,
        0.21555978, -1.164659  , -0.01072499,  0.25348264,  0.91998667,
        0.78019667, -0.80262876, -0.60418725, -0.5218045 ,  0.34904298,
        0.21056768, -0.61423737, -0.41898003,  0.16387308, -0.32760504,
        0.08724087,  0.10142791, -0.584476  , -0.6598056 , -1.2860833 ,
        0.01960207,  0.5520929 ,  1.0267755 ,  0.9918964 , -0.3420815 ,
       -0.363844  , -1.251161  ,  0.8051881 ,  0.07563049,  0.6905947 ,
       -0.82501316, -0.08760668,  0.28936896, -1.4086672 ,  0.3973896 ,
        0.29619396, -0.796109  ,  0.7000313 ,  1.2504762 , -0.8992164 ,
        0.02293098, -0.15823394,  0.524369  , -0.10785196,  0.12231075,
        0.37645486,  0.7174685 , -0.8758828 , -0.11199638, -0.4048347 ,
        0.19373034,  0.02134288, -0.8846459 , -1.3364033 ,  1.00

## Build vectors for the sentences, use for training a model

In [11]:
# Train
X_train = generate_dense_features(tokens, quick_model)
y_train = list(df_train['class_label'])

  0%|                                                                                                                                                                  | 0/53516 [00:00<?, ?it/s]

  0%|                                                                                                                                                          | 3/53516 [00:00<33:55, 26.29it/s]

  0%|                                                                                                                                                          | 6/53516 [00:00<31:34, 28.25it/s]

  0%|                                                                                                                                                         | 10/53516 [00:00<28:08, 31.70it/s]

  0%|                                                                                                                                                         | 16/53516 [00:00<22:51, 39.01it/s]

...

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 53504/53516 [15:27<00:00, 30.20it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 53508/53516 [15:27<00:00, 32.34it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 53512/53516 [15:27<00:00, 32.97it/s]

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 53516/53516 [15:27<00:00, 28.27it/s]

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 53516/53516 [15:27<00:00, 57.67it/s]

In [12]:
# Test
tokens_test = [analyzer(s) for s in list(df_test['tweet_text'])]
tokens_test[100]

['.',
 'to',
 'undertake',
 '#restoration',
 'work',
 'in',
 '2',
 'flood-hit',
 'kerala',
 'villages',
 '#keralafloods',
 '#keralafloodsrelief',
 '. to',
 'to undertake',
 'undertake #restoration',
 '#restoration work',
 'work in',
 'in 2',
 '2 flood-hit',
 'flood-hit kerala',
 'kerala villages',
 'villages #keralafloods',
 '#keralafloods #keralafloodsrelief']

In [13]:
X_test = generate_dense_features(tokens_test, quick_model)
y_test = list(df_test['class_label'])

  0%|                                                                                                                                                                  | 0/15159 [00:00<?, ?it/s]

  0%|                                                                                                                                                          | 3/15159 [00:00<11:23, 22.18it/s]

  0%|                                                                                                                                                          | 6/15159 [00:00<11:07, 22.72it/s]

  0%|                                                                                                                                                          | 9/15159 [00:00<11:25, 22.10it/s]

  0%|▏                                                                                                                                                        | 14/15159 [00:00<08:29, 29.71it/s]

...

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▊| 15135/15159 [03:42<00:00, 59.26it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▊| 15142/15159 [03:42<00:00, 59.64it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 15148/15159 [03:42<00:00, 56.43it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 15156/15159 [03:42<00:00, 59.58it/s]

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 15159/15159 [03:43<00:00, 67.97it/s]

## Train the LR model, score using the test

In [14]:
clf = LogisticRegression(solver='lbfgs', multi_class='auto', random_state=random_seed, max_iter=1000)
clf.fit(X_train, y_train)

LogisticRegression(max_iter=1000, random_state=42)

In [15]:
lr_test_preds = clf.predict(X_test)
f1_lr = f1_score(y_test, lr_test_preds, average='macro')
print(f1_lr)

0.5914428918048563
